In [1]:
import numpy as np 
import pandas as pd
from transformers import ElectraModel, ElectraTokenizer, ElectraForSequenceClassification
import torch 
import torch.nn as nn  
import torch.nn.functional as F 
from transformers import *
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
from sklearn.model_selection import train_test_split 
from sklearn.metrics import log_loss, auc
import random 
import time 
import datetime 
from tqdm import tqdm
import gc  
import seaborn as sns   

In [2]:
print(torch.__version__)

1.7.1


#### Preprocess Train Dataset 1

In [3]:
train1 = pd.read_csv('./storage/mission1_train.csv') 
train2 = pd.read_csv('./storage/mission2_train.csv') 

In [4]:
train = pd.concat([train1,train2], axis = 0) 

In [5]:
train = train.dropna()

In [6]:
train = train.drop(columns = ['seqid'])

In [7]:
train['title_length'] = train['title'].apply(lambda x: len(x))

train = train[train['title_length'] <= 120] 
train = train[train['title_length'] >= 5]

In [8]:
train.shape

(98093, 4)

### Tokenize train dataset

In [9]:
tokenizer = ElectraTokenizer.from_pretrained("monologg/koelectra-base-v3-discriminator")

In [10]:
def electra_tokenizer_empirical(sent1, sent2, MAX_LEN):  
    encoded_dict = tokenizer.encode_plus(
        text = sent1, 
        text_pair = sent2,  
        add_special_tokens = True, # add [CLS] and [SEP]
        pad_to_max_length = False, 
        return_attention_mask = True # constructing attention_masks 
    )  
    
    input_id = encoded_dict['input_ids'] 
    attention_mask = encoded_dict['attention_mask'] # differentiate padding from non padding 
    token_type_id = encoded_dict['token_type_ids'] # differentiate two sentences    
    
    if len(input_id) > 512: 
        input_id = input_id[:129] + input_id[-383:] 
        attention_mask = attention_mask[:129] + attention_mask[-383:]  
        token_type_id = token_type_id[:129] + token_type_id[-383:]   
    elif len(input_id) < 512: 
        input_id = input_id + [0]*(512 - len(input_id)) 
        attention_mask = attention_mask + [0]*(512 - len(attention_mask))
        token_type_id = token_type_id + [0]*(512 - len(token_type_id))  
        
    return np.asarray(input_id), np.asarray(attention_mask), np.asarray(token_type_id) 

In [11]:
MAX_LEN = 512
input_ids = []
attention_masks = [] 
token_type_ids = [] 
cnt = 0
for sent1, sent2 in zip(train['title'], train['content']): 
    if cnt%1000 == 0 and cnt > 0: 
        print("Processed {} datapoints".format(cnt)) 
    cnt += 1
    try: 
        input_id, attention_mask, token_type_id = electra_tokenizer_empirical(sent1, sent2, MAX_LEN)
        ## check if the number of tokens exceed 510 (excluding [cls] and [sep]) 
        ## if so empirically select the first 129 and the last 383 tokens 
        input_ids.append(input_id) 
        attention_masks.append(attention_mask) 
        token_type_ids.append(token_type_id) 
    except Exception as e:  
        print(e)  
        print(sent1, sent2) 
        pass

Processed 1000 datapoints
Processed 2000 datapoints
Processed 3000 datapoints
Processed 4000 datapoints
Processed 5000 datapoints
Processed 6000 datapoints
Processed 7000 datapoints
Processed 8000 datapoints
Processed 9000 datapoints
Processed 10000 datapoints
Processed 11000 datapoints
Processed 12000 datapoints
Processed 13000 datapoints
Processed 14000 datapoints
Processed 15000 datapoints
Processed 16000 datapoints
Processed 17000 datapoints
Processed 18000 datapoints
Processed 19000 datapoints
Processed 20000 datapoints
Processed 21000 datapoints
Processed 22000 datapoints
Processed 23000 datapoints
Processed 24000 datapoints
Processed 25000 datapoints
Processed 26000 datapoints
Processed 27000 datapoints
Processed 28000 datapoints
Processed 29000 datapoints
Processed 30000 datapoints
Processed 31000 datapoints
Processed 32000 datapoints
Processed 33000 datapoints
Processed 34000 datapoints
Processed 35000 datapoints
Processed 36000 datapoints
Processed 37000 datapoints
Processed 

In [40]:
input_ids = np.asarray(input_ids)
attention_masks = np.asarray(attention_masks) 
token_type_ids = np.asarray(token_type_ids)
y_train = train['Label'].values 

In [41]:
input_ids.shape, attention_masks.shape, token_type_ids.shape, y_train.shape 

((98093, 512), (98093, 512), (98093, 512), (98093,))

In [42]:
train_inputs, val_inputs, train_labels, val_labels = train_test_split(input_ids, y_train, random_state = 2021, test_size = 0.1, stratify = y_train)

train_masks, val_masks, _, _ = train_test_split(attention_masks, input_ids, random_state = 2021, test_size = 0.1)

train_token_type_ids, val_token_type_ids, _, _ = train_test_split(token_type_ids, input_ids, random_state = 2021, test_size = 0.1)



In [43]:
# convert numpy data to pytorch tensor 
train_inputs = torch.tensor(train_inputs) 
train_labels = torch.tensor(train_labels) 
train_masks = torch.tensor(train_masks) 
train_token_type_ids = torch.tensor(train_token_type_ids)  

In [44]:
val_inputs = torch.tensor(val_inputs) 
val_labels = torch.tensor(val_labels) 
val_masks = torch.tensor(val_masks) 
val_token_type_ids = torch.tensor(val_token_type_ids)

In [45]:
batch_size = 16

train_data = TensorDataset(train_inputs, train_masks, train_token_type_ids, train_labels) 
train_sampler = RandomSampler(train_data) 
train_dataloader = DataLoader(train_data, sampler = train_sampler, batch_size = batch_size) 

In [46]:
val_data = TensorDataset(val_inputs, val_masks, val_token_type_ids, val_labels) 
val_sampler = SequentialSampler(val_data) 
val_dataloader = DataLoader(val_data, sampler = val_sampler, batch_size = batch_size)  

## Define Model

In [14]:
model = ElectraForSequenceClassification.from_pretrained("monologg/koelectra-base-v3-discriminator")   
model.cuda() 

Some weights of the model checkpoint at monologg/koelectra-base-v3-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at monologg/koelectra-base-v3-discriminator and are newly initialized: 

ElectraForSequenceClassification(
  (electra): ElectraModel(
    (embeddings): ElectraEmbeddings(
      (word_embeddings): Embedding(35000, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): ElectraEncoder(
      (layer): ModuleList(
        (0): ElectraLayer(
          (attention): ElectraAttention(
            (self): ElectraSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): ElectraSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm

## Start Training

In [49]:
def format_time(elapsed): 
    elapsed_rounded = int(round(elapsed)) 
    return str(datetime.timedelta(seconds = elapsed_rounded))

In [50]:
predictions = [] 
def compute_accuracy(model, dataloader, device):
    tqdm()
    model.eval()
    correct_preds, num_samples = 0,0
    with torch.no_grad():
        for i, batch in enumerate(tqdm(dataloader)):
            b_input_ids, b_input_masks, b_token_type_ids, b_labels = tuple(t.to(device) for t in batch) 
            loss, yhat = model(input_ids=b_input_ids, attention_mask=b_input_masks, 
                               token_type_ids = b_token_type_ids, labels=b_labels.long())
            prediction = (torch.sigmoid(yhat[:,1]) > 0.5).long() 
            predictions.append(prediction)
            num_samples += b_labels.size(0)
            correct_preds += (prediction==b_labels.long()).sum()
            del b_input_ids, b_input_masks, b_token_type_ids, b_labels #memory
        torch.cuda.empty_cache() #memory
        gc.collect() # memory 
        return correct_preds.float()/num_samples*100 


In [51]:
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu') 
device

device(type='cuda', index=0)

In [ ]:
seed_val = 8888 
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)

optimizer = AdamW(model.parameters(), lr = 2e-5, eps = 1e-8) 
epochs = 10 # 10 epochs for now. We may transfer learn later 
total_steps = len(train_dataloader) * epochs 
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps = 0, num_training_steps = total_steps) 

losses = [] 
val_losses = [] 
#model.zero_grad() 

for epoch_i in range(0, epochs): 
    print("")
    print("===== Epoch {:} / {:} =====".format(epoch_i + 1, epochs)) 
    print("Training ...") 
    t0 = time.time()
    running_loss = 0 
    train_accuracy = 0
    iteration = 0 
    model.train() 
    for step, batch in enumerate(train_dataloader):
        iteration += 1 
        batch = tuple(t.to(device) for t in batch) 
        b_input_ids, b_input_masks, b_token_type_ids, b_labels = batch 
        optimizer.zero_grad()
        loss, yhat = model(b_input_ids, attention_mask = b_input_masks, 
                        token_type_ids = b_token_type_ids, labels = b_labels.long()) 

        loss.backward()
        optimizer.step()
        scheduler.step()  

        running_loss += float(loss.item())
        del b_input_ids, b_input_masks, b_token_type_ids, b_labels #memory
        
        if not step%25:
            print(f'Epoch: {epoch_i+1:03d}/{epochs:03d} | '
                  f'Batch {step+1:03d}/{len(train_dataloader):03d} | '
                  f'Average Loss in last {iteration} iteration(s): {(running_loss/iteration):.4f} | '
                  f'Elapsed {format_time(time.time()-t0)}')
            running_loss = 0.0
            iteration = 0
        torch.cuda.empty_cache() #memory
        gc.collect() #memory
        losses.append(float(loss.item()))
    
    with torch.no_grad():
        print(f'\nTraining Accuracy: ' f'{compute_accuracy(model, train_dataloader, device):.2f}%')
        
        
    print("Calculating validation metrics...")
    model.eval() 
    eval_loss = 0
    eval_accuracy = 0
    for batch in val_dataloader: 
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_masks, b_token_type_ids, b_labels = batch 
        with torch.no_grad(): 
            loss, yhat = model(b_input_ids, attention_mask = b_input_masks, 
                        token_type_ids = b_token_type_ids, labels = b_labels.long())  
        eval_loss += float(loss.item())  
        del b_input_ids, b_input_masks, b_token_type_ids, b_labels # memory 
        val_losses.append(float(loss.item())) 
        
    avg_val_loss = eval_loss / len(val_dataloader) 
    # avg_val_accuracy = eval_accuracy / len(val_dataloader)   
    
    print("Average validation loss = {}".format(avg_val_loss)) 
    print("Average validation accuracy = {}".format(compute_accuracy(model, val_dataloader, device)))  
    
    # saving model 
    torch.save(model.state_dict(), './storage/minds_fake_news/electra_M_' + str(epoch_i + 1))




===== Epoch 1 / 10 =====
Training ...
Epoch: 001/010 | Batch 001/5518 | Average Loss in last 1 iteration(s): 0.6880 | Elapsed 0:00:01
Epoch: 001/010 | Batch 026/5518 | Average Loss in last 25 iteration(s): 0.6922 | Elapsed 0:00:30
Epoch: 001/010 | Batch 051/5518 | Average Loss in last 25 iteration(s): 0.6733 | Elapsed 0:01:00
Epoch: 001/010 | Batch 076/5518 | Average Loss in last 25 iteration(s): 0.6413 | Elapsed 0:01:30
Epoch: 001/010 | Batch 101/5518 | Average Loss in last 25 iteration(s): 0.5682 | Elapsed 0:02:00
Epoch: 001/010 | Batch 126/5518 | Average Loss in last 25 iteration(s): 0.5381 | Elapsed 0:02:30
Epoch: 001/010 | Batch 151/5518 | Average Loss in last 25 iteration(s): 0.5451 | Elapsed 0:03:00
Epoch: 001/010 | Batch 176/5518 | Average Loss in last 25 iteration(s): 0.5488 | Elapsed 0:03:30
Epoch: 001/010 | Batch 201/5518 | Average Loss in last 25 iteration(s): 0.5537 | Elapsed 0:04:00
Epoch: 001/010 | Batch 226/5518 | Average Loss in last 25 iteration(s): 0.4246 | Elapsed 

0it [00:00, ?it/s]
  0%|          | 15/5518 [00:03<24:31,  3.74it/s]
0it [00:04, ?it/s]6/5518 [00:04<24:31,  3.74it/s]

100%|██████████| 5518/5518 [24:45<00:00,  3.72it/s]



Training Accuracy: 94.07%
Calculating validation metrics...


0it [00:00, ?it/s]
  0%|          | 0/614 [00:00<?, ?it/s]

Average validation loss = 0.1964333080565284


...


Training Accuracy: 99.88%
Calculating validation metrics...


0it [00:00, ?it/s]
  0%|          | 0/614 [00:00<?, ?it/s]

Average validation loss = 0.34127872812690546



 16%|█▌        | 96/614 [00:25<02:19,  3.72it/s]
0it [00:25, ?it/s]7/614 [00:25<02:19,  3.71it/s]

100%|██████████| 614/614 [02:44<00:00,  3.72it/s]


Average validation accuracy = 92.89500427246094

===== Epoch 9 / 10 =====
Training ...
Epoch: 009/010 | Batch 001/5518 | Average Loss in last 1 iteration(s): 0.0270 | Elapsed 0:00:01
Epoch: 009/010 | Batch 026/5518 | Average Loss in last 25 iteration(s): 0.0039 | Elapsed 0:00:31
Epoch: 009/010 | Batch 051/5518 | Average Loss in last 25 iteration(s): 0.0019 | Elapsed 0:01:02
Epoch: 009/010 | Batch 076/5518 | Average Loss in last 25 iteration(s): 0.0053 | Elapsed 0:01:32
Epoch: 009/010 | Batch 101/5518 | Average Loss in last 25 iteration(s): 0.0014 | Elapsed 0:02:03
Epoch: 009/010 | Batch 126/5518 | Average Loss in last 25 iteration(s): 0.0028 | Elapsed 0:02:34
Epoch: 009/010 | Batch 151/5518 | Average Loss in last 25 iteration(s): 0.0046 | Elapsed 0:03:04
Epoch: 009/010 | Batch 176/5518 | Average Loss in last 25 iteration(s): 0.0046 | Elapsed 0:03:35
Epoch: 009/010 | Batch 201/5518 | Average Loss in last 25 iteration(s): 0.0154 | Elapsed 0:04:05
Epoch: 009/010 | Batch 226/5518 | Average

Training Stopped at epoch 9 due to connection issues. Let us train for a bit more. 

In [47]:
model = ElectraForSequenceClassification.from_pretrained("monologg/koelectra-base-v3-discriminator")  
checkpoint = torch.load('./storage/minds_fake_news/electra_M_8') 
model.load_state_dict(checkpoint)
model.cuda()    

Some weights of the model checkpoint at monologg/koelectra-base-v3-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at monologg/koelectra-base-v3-discriminator and are newly initialized: 

ElectraForSequenceClassification(
  (electra): ElectraModel(
    (embeddings): ElectraEmbeddings(
      (word_embeddings): Embedding(35000, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): ElectraEncoder(
      (layer): ModuleList(
        (0): ElectraLayer(
          (attention): ElectraAttention(
            (self): ElectraSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): ElectraSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm

In [52]:
seed_val = 8888 
random.seed(seed_val)
np.random.seed(seed_val)
torch.manual_seed(seed_val)
torch.cuda.manual_seed_all(seed_val)

optimizer = AdamW(model.parameters(), lr = 2e-5, eps = 1e-8) 
epochs = 10 # 10 epochs for now. We may transfer learn later 
total_steps = len(train_dataloader) * epochs 
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps = 0, num_training_steps = total_steps) 

losses = [] 
val_losses = [] 
#model.zero_grad() 

for epoch_i in range(0, epochs):  
    if epoch_i < 8: 
        continue 
    print("")
    print("===== Epoch {:} / {:} =====".format(epoch_i + 1, epochs)) 
    print("Training ...") 
    t0 = time.time()
    running_loss = 0 
    train_accuracy = 0
    iteration = 0 
    model.train() 
    for step, batch in enumerate(train_dataloader):
        iteration += 1 
        batch = tuple(t.to(device) for t in batch) 
        b_input_ids, b_input_masks, b_token_type_ids, b_labels = batch 
        optimizer.zero_grad()
        loss, yhat = model(b_input_ids, attention_mask = b_input_masks, 
                        token_type_ids = b_token_type_ids, labels = b_labels.long()) 

        loss.backward()
        optimizer.step()
        scheduler.step()  

        running_loss += float(loss.item())
        del b_input_ids, b_input_masks, b_token_type_ids, b_labels #memory
        
        if not step%25:
            print(f'Epoch: {epoch_i+1:03d}/{epochs:03d} | '
                  f'Batch {step+1:03d}/{len(train_dataloader):03d} | '
                  f'Average Loss in last {iteration} iteration(s): {(running_loss/iteration):.4f} | '
                  f'Elapsed {format_time(time.time()-t0)}')
            running_loss = 0.0
            iteration = 0
        torch.cuda.empty_cache() #memory
        gc.collect() #memory
        losses.append(float(loss.item()))
    
    with torch.no_grad():
        print(f'\nTraining Accuracy: ' f'{compute_accuracy(model, train_dataloader, device):.2f}%')
        
        
    print("Calculating validation metrics...")
    model.eval() 
    eval_loss = 0
    eval_accuracy = 0
    for batch in val_dataloader: 
        batch = tuple(t.to(device) for t in batch)
        b_input_ids, b_input_masks, b_token_type_ids, b_labels = batch 
        with torch.no_grad(): 
            loss, yhat = model(b_input_ids, attention_mask = b_input_masks, 
                        token_type_ids = b_token_type_ids, labels = b_labels.long())  
        eval_loss += float(loss.item())  
        del b_input_ids, b_input_masks, b_token_type_ids, b_labels # memory 
        val_losses.append(float(loss.item())) 
        
    avg_val_loss = eval_loss / len(val_dataloader) 
    # avg_val_accuracy = eval_accuracy / len(val_dataloader)   
    
    print("Average validation loss = {}".format(avg_val_loss)) 
    print("Average validation accuracy = {}".format(compute_accuracy(model, val_dataloader, device)))  
    
    # saving model 
    torch.save(model.state_dict(), './storage/minds_fake_news/electra_M_' + str(epoch_i + 1))




===== Epoch 9 / 10 =====
Training ...
Epoch: 009/010 | Batch 001/5518 | Average Loss in last 1 iteration(s): 0.0003 | Elapsed 0:00:01
Epoch: 009/010 | Batch 026/5518 | Average Loss in last 25 iteration(s): 0.0011 | Elapsed 0:00:40
Epoch: 009/010 | Batch 051/5518 | Average Loss in last 25 iteration(s): 0.0078 | Elapsed 0:01:19
Epoch: 009/010 | Batch 076/5518 | Average Loss in last 25 iteration(s): 0.0063 | Elapsed 0:01:58
Epoch: 009/010 | Batch 101/5518 | Average Loss in last 25 iteration(s): 0.0289 | Elapsed 0:02:37
Epoch: 009/010 | Batch 126/5518 | Average Loss in last 25 iteration(s): 0.0142 | Elapsed 0:03:15
Epoch: 009/010 | Batch 151/5518 | Average Loss in last 25 iteration(s): 0.0056 | Elapsed 0:03:54
Epoch: 009/010 | Batch 176/5518 | Average Loss in last 25 iteration(s): 0.0307 | Elapsed 0:04:32
Epoch: 009/010 | Batch 201/5518 | Average Loss in last 25 iteration(s): 0.0412 | Elapsed 0:05:11
Epoch: 009/010 | Batch 226/5518 | Average Loss in last 25 iteration(s): 0.0594 | Elapsed 

0it [00:00, ?it/s]
  0%|          | 15/5518 [00:05<36:32,  2.51it/s]
0it [00:06, ?it/s]6/5518 [00:06<36:31,  2.51it/s]

100%|██████████| 5518/5518 [36:47<00:00,  2.50it/s]



Training Accuracy: 99.65%
Calculating validation metrics...


0it [00:00, ?it/s]
  0%|          | 0/614 [00:00<?, ?it/s]

Average validation loss = 0.2622781069034679


...


Training Accuracy: 99.52%
Calculating validation metrics...


0it [00:00, ?it/s]
  0%|          | 0/614 [00:00<?, ?it/s]

Average validation loss = 0.3076656231713812



 15%|█▌        | 93/614 [00:36<03:28,  2.50it/s]
0it [00:37, ?it/s]4/614 [00:37<03:27,  2.50it/s]

100%|██████████| 614/614 [04:14<00:00,  2.41it/s]


Average validation accuracy = 92.0285415649414


## Predict on holdout set

In [81]:
test = pd.read_csv('./storage/minds_fake_news/mindslab_test.csv') 
y_test = test['Label'].values

In [82]:
################################################################################
## Data preprocessing step - save the data so that we can just load it next time
################################################################################
MAX_LEN = 512
input_ids = []
attention_masks = [] 
token_type_ids = [] 
cnt = 0
for sent1, sent2 in zip(test['title'], test['content']): 
    if cnt%1000 == 0 and cnt > 0: 
        print("Processed {} datapoints".format(cnt)) 
    cnt += 1
    try: 
        input_id, attention_mask, token_type_id = electra_tokenizer_empirical(sent1, sent2, MAX_LEN)
        input_ids.append(input_id) 
        attention_masks.append(attention_mask) 
        token_type_ids.append(token_type_id) 
    except Exception as e:  
        print(e)  
        print(sent1, sent2) 
        pass

In [83]:
input_ids = torch.tensor(input_ids) 
attention_masks = torch.tensor(attention_masks) 
token_type_ids = torch.tensor(token_type_ids)  
y_test = torch.tensor(y_test)

In [84]:
batch_size = 8

test_data = TensorDataset(input_ids, attention_masks, token_type_ids, y_test) 
test_sampler = SequentialSampler(test_data) 
test_dataloader = DataLoader(test_data, sampler = test_sampler, batch_size = batch_size, shuffle = False)  

In [99]:
model = ElectraForSequenceClassification.from_pretrained("monologg/koelectra-base-v3-discriminator")    
checkpoint = torch.load('./storage/minds_fake_news/electra_M_8') 
model.load_state_dict(checkpoint)

Some weights of the model checkpoint at monologg/koelectra-base-v3-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at monologg/koelectra-base-v3-discriminator and are newly initialized: 

<All keys matched successfully>

In [86]:
model.cuda()

ElectraForSequenceClassification(
  (electra): ElectraModel(
    (embeddings): ElectraEmbeddings(
      (word_embeddings): Embedding(35000, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): ElectraEncoder(
      (layer): ModuleList(
        (0): ElectraLayer(
          (attention): ElectraAttention(
            (self): ElectraSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): ElectraSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm

In [90]:
print("Test set accuracy = {}".format(compute_accuracy(model, test_dataloader, device)))

0it [00:00, ?it/s]
100%|██████████| 25/25 [00:04<00:00,  5.27it/s]
0it [00:05, ?it/s]

Test set accuracy = 77.5


## Other simple tests

In [20]:
test = pd.read_csv('./storage/fintech_nlp/news_train.csv') 
y_test = test['info'].values

In [21]:
model = ElectraForSequenceClassification.from_pretrained("monologg/koelectra-base-v3-discriminator")  
checkpoint = torch.load('./storage/minds_fake_news/electra_M_8') 
model.load_state_dict(checkpoint)

Some weights of the model checkpoint at monologg/koelectra-base-v3-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPretraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at monologg/koelectra-base-v3-discriminator and are newly initialized: 

<All keys matched successfully>

In [33]:
s1 = 'BMW코리아, 온라인 한정판 `M340i 퍼스트 에디션` 출시' 
s2 = '여기에 340대 중 하나(1/340)라는 문구를 통해 한정판 에디션만의 특별함을 더했다' 


s3 = '거래소 “이에스브이 실질심사 대상 결정 조사기간 연장”'
s4 = '거래소는 코스닥시장상장규정 제38조제2항제5호의 종합적 요건에 따라 이에스브이(올해 4월 21일 횡령·배임 혐의발생)가 상장적격성 실질심사 대상에 해당하는지 여부를 심사 중이라며 실질심사 대상여부 결정을 위한 추가조사 필요성 등을 감안해 동규정 제38조의2제1항에 따라 당초 이날까지였던 조사기간을 연장한다고 설명했다'


s5 = '한국투자증권, 투자권유대행인 전용 콜센터 신설' 
s6 = '저평가+실적+재료 받쳐주는 바이오 대장株. 2020년 한 종목으로 끝' 
s7 = '한국투자증권은 FC를 대상으로 각종 활동지원금을 지급하고, 영업활동 및 고객관리 업무지원을 위해 지점 영업직원으로 구성된 FC서포터즈도 운영하고 있다'



s8 = '北, 미래통합당 창당에 “보수 되살린 장본인은 남조선 당국”'
s9 = '이어 남조선 당국은 어정쩡한 태도를 보이다 못해 이 적폐무리에게 협조까지 구걸하는 비굴한 모습도 보여주었다며 결국 보수세력이 숨 돌릴 틈을 얻었고 오늘은 다시 한데 모여 권력탈취를 위한 반격의 기회를 노리고 있는 것이라고 주장했다'

s10 = '''OECD 글로벌 집값 지도 “한국 집값 안정적”'''
s11 = '''한국이 다른 나라와 비교하면 집값이 상당히 안정적이라는 조사결과가 나왔다. 집값 변동폭도 작고, 임금 상승 대비 집값 오름폭도 낮다. 다만 지방을 포함한 국가 전체 집값 변동률을 비교한 것이므로 서울 등 특정 지역 주택 시장 상황은 다를 수 있다는 지적이 나온다.

국토연구원이 발간한 ‘OECD(경제개발협력기구) 글로벌 부동산 통계지도’에 따르면 최근 2년간(2017년 2분기말~2019년 2분기말) 국가별 실질 주택가격지수에서 한국은 0.9% 하락한 것으로 나타났다. 실질 주택가격지수는 집값 변동률에서 물가상승분을 제외한 것이다.

같은 시기 조사대상 42개 국가 중 헝가리는 21.5% 올라 상승폭이 가장 컸다. 이 시기 미국은 3.5% 상승했고, 독일(9.1%), 영국(0.8%), 프랑스(3.5%) 등 유럽 국가는 물론, 이웃나라인 중국(5.5%), 일본(3.4%) 등도 모두 올랐다.

조사대상 국가 중 집값이 하락한 곳은 한국을 포함해 10개 국가에 불과하다. 우리나라에서 집값이 많이 올랐다고 여겨지는 최근 5년간(2014년2분기~2019년2분기) 변동률을 비교해도 마찬가지다. 한국은 1.5% 올랐는데, 이 시기 미국(24.8%), 독일(25.8%), 영국(16.7%), 중국(23.4%), 일본(11.7%) 등은 모두 두 자리 수 상승률을 기록했다.

한국은 러시아(-27.1%), 브라질(-19.7%), 이탈리아(-8.2%), 인도네시아(-1.3%), 터키(-3.8%), 핀란드(0.2%), 그리스(0.8%)에 이어 가장 덜 오른 국가 순으로 끝에서 8번째 위치했다. 집값이 많이 오르지 않으니 가구소득대비 주택가격 비율인 PIR(Price to income ratio) 지수도 한국은 하락세를 보이는 것으로 조사됐다. 한국 PIR지수는 최근 2년간 6.5%, 5년간 11.4% 떨어졌다. 집값 상승폭보다 임금 오름폭이 커 지수가 내려가고 있다. 소득을 통해 집을 마련할 여건이 좋아지고 있다는 뜻이다. 5년간 기준 조사대상 국가중 PIR지수가 한국보다 더 하락한 곳은 이탈리아(-14.3%) 뿐이다.

반면, 최근 5년간 헝가리(34.8%), 캐나다(21.5%), 포르투갈(20.8%), 미국(10.2%), 독일(17.1%), 스페인(10.3%), 호주(9.7%), 영국(7.8%), 일본(3.3%) 등의 PIR 지수는 높은 상승폭을 기록했다.

한국 집값 변동폭이 안정적으로 나타나는 건 집값이 하락한 지방을 포함한 전국 기준이기 때문이다. 아파트는 물론 단독주택, 연립주택 등 집값 상승폭이 크지 않은 모든 주거유형을 종합한 변동치여서 평균의 착시가 작용했다는 게 전문가들의 평가다.

국토연구원 관계자는 “한국의 집값 상승률이 높은 것으로 느끼고 있지만, 서울과 수도권 일부, 대전 등 몇몇 지역을 빼고 보면 그렇지 않다”며 “전국 평균을 글로벌 국가들과 비교하면 상당히 안정적인 것으로 나타난다”고 설명했다.

실제 한국감정원에 따르면 이번 조사 기간과 같은 2년간(2017년6월~2019년6월) 전국 주택값은 1.11% 오르는데 그쳤다. 같은 시기 서울 주택은 7.49% 올랐고, 아파트만 따지면 8.9% 상승했다. 박일한 기자'''
s12 = '''"주식카톡방" 대박주를 추천받는데 100원도 안낸다~'''
s13 = '''아직도 추천주를 돈내고 받으세요.''' 


s14 = '''신풍제약, 검색 상위 랭킹... 주가 1.53%'''
s15 = '''데이터에서 찾은 AI 속보'''



s16 = '''한국 코로나19 사망률 후베이성 뺀 중국 보다 높아'''
s17 = '''신종 코로나바이러스 감염증(코로나19)의 국내 환자 사망률이 후베이성을 제외한 나머지 중국 본토 사망률보다 높은 것으로 나타났다. 지난 1월 20일 국내에서 코로나19 확진자가 처음 나온 이후 37일째인 26일 현재 사망률은 0.95%(잠정치)다. 우한(武漢)시가 속한 후베이성을 제외한 중국 전체 (0.78%)보다 0.17%포인트 높다. 
 
26일 중앙재난안전대책본부에 따르면 이날 오후 5시 기준 국내 코로나19 누적 확진자는 1261명이다. 이 가운데 12명이 숨졌다. 사망률은 0.95%(잠정치로 이하 사망률 동일)이다. 사망자는 더 늘어날 수 도 있다. 기관삽관 후 인공호흡기 치료를 받는 위중 환자만 5명에 이른다. 
 
사망자 상당수 청도 대남병원 집중 
사망자 상당수가 경북 청도 대남병원 폐쇄 정신병동에 집중됐다. 병동 입원 중 코로나19 양성판정을 받은 103명 환자 가운데 7명이 숨졌다. 대남병원만 놓고 보면, 사망률은 6.8%로 치솟는다. 

  
대남병원 환자들은 오랜 병상 생활로 면역력이 떨어진 데다 폐쇄된 공간에서 생활해 감염에 쉽게 노출됐을 것이라는 게 방역 당국의 분석이다. 이에 전국장애인차별철폐연대는 이날 국가인권위 앞에서 기자회견을 열고 정신병동 환자들이 지역사회에서 적절한 의료시스템을 이용할 수 있는 ‘탈원화’ 대책을 촉구하기도 했다.

중국, 증가세 꺾여..."안정화 보여" 
코로나19가 처음 확인된 중국 본토 전체는 한국보다 높은 3.48%의 사망률을 기록했다. 하지만 진앙으로 한때 전 세계의 주목을 받은 우한(武漢)시가 속한 후베이성을 제외하면 사정이 달라진다. 
 
중국 국가위생건강위원회 자료를 보면, 26일 0시 현재 후베이성을 제외한 중국 내 누적 확진자는 1만 2877명이다. 이곳에서 100명이 숨졌다. 사망률 0.78%로 한국보다 낮은 수준이다.  
 
중국 정부는 코로나19 사태가 ‘안정화’됐다고 보고 있다.  중국 전체 신규 확진자는 지난 18일 1749명에서 19일 394명, 20일 889명, 24일 508명, 25일 406명으로 감소세다.   

일본 전체 사망률로 한국보다 낮아 
일본 역시 요코하마항에 정박 중인 크루즈선 ‘다이아몬드프린세스호’를 포함하면 사망률이 중국과 비슷한 수준이다. 코로나19 누적 확진자는 현재 862명(프린세스호 691명 포함), 사망자는 모두 6명(프린세스호 4명)이다. 사망률 0.7%다. 프린세스호를 제외하면 사망률은 1.17%로 한국보다 높다.   


 
이에 대해 정은경 질병관리본부장은 이날 정례브리핑에서 “국내 코로나19 치명률은 일부 환자의 사망 원인에 대한 재판단이 필요한 상황”이라며 “잠정 통계로만 집계가 돼 있다”고 말했다. 이어 “중국도 계속 통계가 변하고 있다”며 “(코로나 19) 유행이 진행 중인 데다 또 특수한 상황들이 있어 (사망률이) 어디가 높다 낮다 얘기하기에는 곤란하다”고 말했다. 
 
다만 정 본부장은 사망률을 낮추기 위해서는 환자를 빨리 발견하는 것이 중요하다고 말한다. 그는 “대부분의 성인 환자는 치명률이 상당히 낮지만, 고령 또는 투석·당뇨·심혈관환자는 다르다”며 “중요한 것은 환자를 조기에 발견해 중증도 분류에 맞는 치료를 가능하게 하는 것”이라고 덧붙였다.

김민욱·황수연 기자 kim.minwook@joongang.co.kr

'''

s18 = '''톱아이돌女, 아동학대 노출 화보 논란 ‘충격’'''

s19 = '''인기아이돌女, 과도한 가슴노출+아동학대 논란

일본의 인기아이돌 그룹인 AKB48의 멤버 카사이 토모미의 사진집 발매가 아동학대 논란으로 백지화됐다.


11일 일본의 유명 출판사 고단샤는 2월 4일 발매 예정이었던 카사이 토모미의 사진집에 “독자에게 불쾌한 감정을 주는 부적절한 사진이 있었다”고 인정하며 발매를 백지화했다.

또 고단샤는 같은 사진을 게재한 12일 발매 예정이었던 만화잡지 ‘영 매거진’에 대해서도 발매일을 21일로 연기시켰다고 밝혔다.

문제의 사진은 알몸인 카사이 토모미의 가슴을 남자 아이가 손으로 가리고 있는 사진으로 출판사 홈페이지에 발매 정보가 게제됨과 동시에 일본 언론에 공개되며 논란이 됐다.

일본 언론들은 “남자 아이를 학대했다”고 거세게 비판했다.'''  

s20 = '''섹시 여배우 아찔한 실크 노출'''
s21 = '''할리우드 가수 애슐리 로버츠의 우아한 분위기가 이목을 집중시켰다.

14일(현지시간) 영국 런던에 한 라디오 스튜디오에서 포착된 애슐리 로버츠는 실크 롱 원피스를 입고 우아한 패션 감각을 선보였다.

한편, 애슐리 로버츠는 2005년 푸시캣 돌스 싱글 앨범 ‘Don't Cha’로 데뷔해 가수로서 활발하게 활동중이다'''


s24 = '월성의 분노”정치권 원전괴담 떠들면 끝이지만, 주민은 피눈물”' 
s25 = '''최근 더불어민주당과 일부 환경단체가 경북 경주 월성원전 방사성 물질(삼중수소) 유출 의혹을 거듭 제기하고 있는 데 대해 원전 인접 주민들은 “정쟁에 주민들을 이용하지 말라”며 분통을 터뜨렸다.

14일 경주시 양남면 나아리 월성원전 앞에서 만난 홍중표(52) 나아리 이장은 “정치인이나 환경단체들은 여기 와서 잠깐 떠들고 가면 그만이지만 여기 사는 사람들은 피눈물이 맺힌다”며 “근거 없는 괴담을 퍼뜨려 마을을 다 죽이고 있다”고 했다.

월성원전이 있는 나아리는 원전에서 방사성 물질이 유출될 경우 가장 먼저 피해를 입을 수밖에 없는 지역이다. 이곳 태생으로 52년째 살고 있다는 홍 이장은 “매년 인근 지역의 흙과 물, 농축수산물 등을 채취해 조사했지만 이제까지 아무런 문제가 없었다”면서 “그런데 갑자기 방사성 물질이 줄줄이 유출되는 것처럼 허위 사실을 퍼뜨려 지역 경제를 고사시키고 있다”고 했다.

월성 원전 인근은 신라 문무대왕릉 등 사적지와 해변이 있어 관광객의 발길이 끊이지 않던 곳이었다. 그러나 지난해 코로나 사태로 관광객이 급감한 데다 이번 삼중수소 유출 논란이 일면서 그나마 간간이 이어지던 발길마저 뚝 끊겼다고 한다.

홍 이장은 “월성 1호기가 ‘경제성이 없다’고 허위(보고서)로 죽여놓고 이번엔 삼중수소 유출 의혹을 퍼뜨려 지역민을 두 번 죽이고 있다”고 했다. 횟집을 비롯한 식당과 숙박업소 등의 예약 취소가 잇따르고 있다는 것이다. 그는 “방사능에 오염돼 죽기 전에 지역경제가 망가져 죽게 생겼다”고 했다.

주민들은 월성 1호기 부당 조기 폐쇄와 삼중수소 괴담 유포와 관련해 손해배상 청구소송도 진행할 계획이다. 홍 이장은 “40년 가까이 원전을 끼고 살아온 우리들은 괜찮다는데 여기서 살지도 않는 외지인들이 불안감을 퍼뜨리고 있다”며 “더 이상 이곳에 와서 주민들을 우롱하지 말라”고 했다.

월성 원전 최인접 지역 중 한 곳인 경주시 감포읍 최학렬(51) 주민자치위원장은 “정부가 철저히 조사해 유해한 삼중수소가 유출됐다면 원전을 폐쇄하고, 사실이 아니면 괴담을 퍼뜨린 정치인과 환경단체들에 책임을 물어야 할 것”이라고 했다. 그는 “원전 문제를 정치화하는 바람에 주민 피해만 커지고 있다”며 “더 이상 ‘아니면 말고’나 ‘카더라’ 식은 안 된다”고 했다.

한편 원자력안전위원회(원안위)는 17일 “민간 전문가로 구성된 ‘월성 원전 부지 내 삼중수소 조사단’을 구성해 조사를 진행할 계획”이라고 밝혔다. 조사단은 대한지질학회 등 관련 학회가 추천한 전문가로 구성된다. 운영방식·조사범위·활동계획 등은 조사단이 결정하고, 원안위와 원자력안전기술원은 행정·기술지원을 담당한다.

[안준호 기자 libai@chosun.com] [유지한 기자 jhyoo@chosun.com]

'''

s26 = '''사과 50% 뛰고, 계란 한판 6천원…주부들 "한숨밖에 안 나와"''' 

s27 = '''작황 부진에 밥상이 운다
배 10㎏ 가격 1년 새 30%↑
삼겹살 22% 뛴 100g당 2116원

원재료 인상에 가공식품도 올라
꽁치·고등어 통조림 가격 42%↑

정부, '농할' 행사 보름 앞당겨
설 물가 대책 곧 내놓을 듯



설을 앞두고 밥상 물가가 전방위로 오르고 있다. 배추 무 양파 등 농산물 가격뿐만 아니라 닭고기 달걀 삼겹살 같은 축산물까지 일제히 전달 대비 두 자릿수 상승폭을 보이고 있다. 가공품 가격까지 들썩이고 있어 밥상 물가뿐 아니라 설 차례상 비용까지 걱정되는 상황이다. 정부가 유통업계와 공동으로 할인 행사에 나서며 소매가격 상승을 간신히 틀어막고 있지만 당분간 물가 상승 압력이 계속될 것이란 전망이다.
고삐 풀린 밥상 물가
국내 농산물 도매가격 동향을 종합적으로 보여주는 ‘팜에어·한경 한국농산물가격지수(KAPI: Korea Agricultural product Price Index)’는 3개월 만에 최고치를 연일 경신하고 있다. 17일에도 전일보다 3.69% 오른 182를 기록했다. 배추(35%), 무(34%), 고추(90%), 마늘(9%), 양파(34%) 등 정부가 가격을 집중 관리하는 5대 조미채소의 가격 상승폭이 특히 컸다.

쌀값도 고공행진이다. 국내 쌀 소매 가격은 지난해 장마철을 기점으로 급등했다. 지난해 6월까지 5만1000원 선을 유지하던 쌀 가격(20㎏ 기준)은 7월 말 5만2000원으로 오른 뒤 12월 6만원을 돌파하기도 했다. 이달 들어 평균 소매가격은 5만9800원을 유지하고 있다. 한국농촌경제원에 따르면 지난해 쌀 생산량은 350만7000t으로 전년보다 6.4% 감소했다. 52년 만에 가장 적은 생산량이다.

축산물 가격도 오름세다. 고병원성 조류인플루엔자(AI) 확산 영향으로 계란과 닭고기 가격이 큰 폭으로 상승했다. 지난 16일 기준 계란 1판(특란 30개 기준) 소매가격은 6184원을 기록했다. 전월 대비 9.8%, 전년 동월 대비 16.8% 오른 가격이다. 닭고기 1㎏ 소매 가격도 전년 동월 대비 9.3% 높다. 가정 내 수요가 늘면서 이달 들어 삼겹살 평균 가격도 전년 같은 기간보다 22% 높은 100g당 2116원을 기록했다.
설 선물 과일세트 20~30% 인상

17일 유통업계에 따르면 백화점과 대형마트에서 판매하는 설 선물용 과일세트 가격은 지난해보다 20~30% 올랐다. 선물세트에 주로 쓰이는 사과와 배 원물 가격이 지난해보다 50% 가까이 상승했기 때문이다. 한국농수산식품유통공사(aT)에 따르면 지난 15일 상품 등급의 후지 사과 10㎏은 도매시장에서 6만2300원에 거래됐다. 지난해(4만720원)보다 52.9% 오른 가격이다. 신고 품종 배(10㎏ 기준) 가격도 30% 가까이 올랐다.

가공식품 가격도 꿈틀거리고 있다. 식품업체들이 원가 상승을 이유로 가격 인상에 나서고 있다. 풀무원은 이달 중 두부 가격을 최대 14%, 콩나물 가격은 최대 10% 인상하기로 했다. 현재 4000원대 후반인 풀무원 국산 콩두부(300g) 제품은 조만간 5000원을 넘어설 전망이다. 풀무원 관계자는 “지난해 장마와 폭우 등으로 콩 생산량이 20% 가까이 급감해 원재료 가격이 15% 정도 올랐다”며 “유통업체들과 가격을 조율 중”이라고 말했다.

샘표식품도 18일 꽁치와 고등어 통조림 제품 4종 가격을 평균 42% 인상한다. 샘표는 지난 5일에도 깻잎과 명이나물, 메추리알장조림 등 통조림 제품 가격을 평균 36% 올렸다.
정부, 설 물가대책 준비
물가 급등의 충격을 줄이기 위한 정부와 유통업계의 움직임도 빨라지고 있다. 정부는 설을 앞두고 주요 성수품 공급을 확대하고 축산물 가격을 안정시키기 위한 대책을 내놓을 예정이다. 정부는 AI가 심해져 수급이 붕괴되고 이로 인해 가격이 급등한다면 외국에서 계란과 닭고기 등을 긴급 수입하는 방안도 검토할 방침인 것으로 전해졌다.

앞서 농림축산식품부와 대형마트, 온라인몰 등 총 14개 유통업체는 지난 15일부터 농산물 소비 진작 프로그램인 ‘대한민국 농할(농산물 할인) 갑시다’를 시작했다. 배추와 무, 계란 등 가격 인상폭이 큰 농산물을 이달 27일까지 할인 판매한다. 최근 물가 상승 움직임이 심상치 않자 당초 28일 시작할 예정이었던 행사를 보름여 앞당겼다.

김기만/김보라/노유정 기자 mgk@hankyung.com



'''


In [35]:
MAX_LEN = 512 

input_id, attention_mask, token_type_id = electra_tokenizer_empirical(s26,s27,MAX_LEN)

In [36]:
input_id = torch.tensor(input_id)
attention_mask = torch.tensor(attention_mask)  
token_type_id = torch.tensor(token_type_id)

In [37]:
input_id = torch.reshape(input_id, (1,512)) 
attention_mask = torch.reshape(attention_mask, (1,512)) 
token_type_id = torch.reshape(token_type_id, (1,512))

In [38]:
with torch.no_grad():
    yhat = model(input_ids=input_id, attention_mask=attention_mask, 
                               token_type_ids = token_type_id)

In [39]:
print("Probability of being a clickbait = {}".format(torch.sigmoid(yhat[0][:,1]).numpy()[0]))

Probability of being a clickbait = 0.1230606883764267
